In [46]:
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.utils.class_weight import  compute_sample_weight
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import accuracy_score

from xgboost import XGBClassifier

from hyperopt import STATUS_OK, Trials, fmin, hp, tpe

In [47]:
train_df = pd.read_csv('data/ml_training.txt', index_col=[0])
test_df = pd.read_csv('data/ml_testing.txt', index_col=[0])

In [48]:
df_corr=train_df.corr().abs().stack().reset_index().sort_values(0, ascending=False)
df_corr['pairs'] = list(zip(df_corr.level_0, df_corr.level_1))
df_corr.set_index(['pairs'], inplace = True)
df_corr.drop(columns=['level_1', 'level_0'], inplace = True)
df_corr.columns = ['cc']
df_corr.drop_duplicates(inplace=True)
df_corr = df_corr[df_corr['cc'] < 1.0000]
df_corr.head(10)

cc
pairs                                                       
(source_class_non_functional, source_class_func...  0.997228
(extraction_type_functional, extraction_type_gr...  0.997188
(quantity_non_functional, quantity_group_functi...  0.996439
(quantity_non_functional, quantity_functional)      0.996439
(waterpoint_type_group_functional, waterpoint_t...  0.996435
(quality_group_non_functional, quality_group_fu...  0.996039
(quality_group_functional, water_quality_functi...  0.995305
(extraction_type_group_non_functional, extracti...  0.995145
(waterpoint_type_functional, waterpoint_type_no...  0.994970
(water_quality_functional, quality_group_non_fu...  0.991363

In [49]:
corr_feats = set()
corr = train_df.corr()

for i in range(len(corr.columns)):
    for j in range(i):
        if abs(corr.iloc[i, j]) > 0.85:
            colname = corr.columns[i]
            corr_feats.add(colname)

In [50]:
train_df = train_df.drop(corr_feats, axis=1)
test_df = test_df.drop(corr_feats, axis=1)

In [52]:
unwanted_cols = ['Unnamed: 0', 'id']
train_df.drop(unwanted_cols, axis=1, inplace=True)
test_df.drop(unwanted_cols, axis=1, inplace=True)

In [54]:
cols = [col for col in train_df.columns.tolist() if col != 'status_group']

test_df = test_df.reindex(columns=[col for col in train_df.columns]).drop('status_group', axis=1)

test_df.columns.tolist() == cols

True

In [56]:
X = train_df.drop(['status_group'], axis=1).select_dtypes(['int', 'float'])
y = train_df['status_group']

sample_weights = compute_sample_weight('balanced', y)

le = LabelEncoder()
y = le.fit_transform(y)

X_train_, X_test_, y_train_, y_test_ = train_test_split(X,y, random_state=42, stratify=y)
X_val, X_test_, y_val, y_test_ = train_test_split(X_test_, y_test_, random_state=42, stratify=y_test_)

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train_)
X_test = scaler.transform(X_test_)

rf = RandomForestClassifier(random_state=42, n_jobs=-1)

rf.fit(X_train, y_train_)
y_hat_train = rf.predict(X_train)
y_hat = rf.predict(X_test)

print('Train Accuracy Score:', accuracy_score(y_hat_train, y_train_))
print('Test Accuracy Score:', accuracy_score(y_test_, y_hat))

Train Accuracy Score: 0.9994163860830527
Test Accuracy Score: 0.829248586049017


In [57]:
xgb = XGBClassifier(use_label_encoder=False, \
                    n_jobs=-1,
                    tree_method='gpu_hist',
                    objective='multi:softprob',
                    sample_weight=sample_weights)

watchlist = [(X_train_, y_train_), (X_val, y_val)]

xgb.fit(X_train_, y_train_, eval_set=watchlist, eval_metric='merror')

y_hat = xgb.predict(X_test_)
print('Train Accuracy score:', accuracy_score(y_hat_train, y_train_))
# print('Accuracy score:', accuracy_score(y_test, y_hat))
print('Test Accuracy Score:', accuracy_score(y_test_, y_hat))

[13:02:32] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learner.cc:576: 
Parameters: { "sample_weight" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-merror:0.20427	validation_1-merror:0.20320
[1]	validation_0-merror:0.20094	validation_1-merror:0.19987
[2]	validation_0-merror:0.19450	validation_1-merror:0.19440
[3]	validation_0-merror:0.19095	validation_1-merror:0.19224
[4]	validation_0-merror:0.18923	validation_1-merror:0.18883
[5]	validation_0-merror:0.18599	validation_1-merror:0.18479
[6]	validation_0-merror:0.18424	validation_1-merror:0.18272
[7]	validation_0-merror:0.18238	validation_1-merror:0.18183
[8]	validation_0-merror:0.18072	validation_1-merror:0.18111
[9]	validation_0-merror

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


[12]	validation_0-merror:0.17621	validation_1-merror:0.17841
[13]	validation_0-merror:0.17594	validation_1-merror:0.17761
[14]	validation_0-merror:0.17380	validation_1-merror:0.17536
[15]	validation_0-merror:0.17286	validation_1-merror:0.17410
[16]	validation_0-merror:0.17203	validation_1-merror:0.17357
[17]	validation_0-merror:0.17109	validation_1-merror:0.17366
[18]	validation_0-merror:0.17037	validation_1-merror:0.17366
[19]	validation_0-merror:0.16853	validation_1-merror:0.17123
[20]	validation_0-merror:0.16810	validation_1-merror:0.17087
[21]	validation_0-merror:0.16739	validation_1-merror:0.17051
[22]	validation_0-merror:0.16678	validation_1-merror:0.17033
[23]	validation_0-merror:0.16548	validation_1-merror:0.16979
[24]	validation_0-merror:0.16496	validation_1-merror:0.16934
[25]	validation_0-merror:0.16391	validation_1-merror:0.16997
[26]	validation_0-merror:0.16382	validation_1-merror:0.16979
[27]	validation_0-merror:0.16281	validation_1-merror:0.16934
[28]	validation_0-merror

In [ ]:
def score(params):
    print("Training with params: ")
    print(params)
    watchlist = [(X_train_, y_train_), (X_val, y_val)]
    gbm_model = XGBClassifier(
        use_label_encoder=False,
        n_estimators = int(params['n_estimators']),
        max_depth= params['max_depth'],
        min_child_weight= params['min_child_weight'],
        subsample= params['subsample'],
        gamma= params['gamma'],
        colsample_bytree= params['colsample_bytree'],
        eta= params['eta'],
        eval_metric= 'merror',
        objective= 'multi:softprob',
        tree_method='gpu_hist',
        booster= 'gbtree',
        silent= 1,
        seed= 42,
        # num_class= 3,
        sample_weight=sample_weights
    )
    gbm_model.fit(X_train_, y_train_,
                  eval_set=watchlist)
    predictions = gbm_model.predict(X_test_)

    score_ = cross_val_score(gbm_model, X_train_, y_train_, cv=5, scoring='accuracy', n_jobs=-1).mean()

    print("\tScore {0}\n\n".format(score_))

    return {'loss': -score_, 'status': STATUS_OK}


def optimize(trials):
    """
    This is the optimization function that given a space (space here) of
    hyperparameters and a scoring function (score here), finds the best hyperparameters.
    """

    space = {
        'n_estimators': hp.quniform('n_estimators', 10, 1000, 1),
        'eta': hp.quniform('eta', 0.025, 0.5, 0.025),
        'max_depth':  hp.choice('max_depth', np.arange(1, 20, dtype=int)),
        'min_child_weight': hp.quniform('min_child_weight', 1, 6, 1),
        'subsample': hp.quniform('subsample', 0.5, 1, 0.05),
        'gamma': hp.quniform('gamma', 0.5, 1, 0.05),
        'colsample_bytree': hp.quniform('colsample_bytree', 0.5, 1, 0.05),
    }
    # Use the fmin function from Hyperopt to find the best hyperparameters
    best = fmin(score, \
                space, \
                algo=tpe.suggest, \
                trials=trials, \
                max_evals=500)
    return best

trials = Trials()

best_hyperparams = optimize(trials)

Training with params:                                  
{'colsample_bytree': 0.9, 'eta': 0.35000000000000003, 'gamma': 0.65, 'max_depth': 14, 'min_child_weight': 2.0, 'n_estimators': 312.0, 'subsample': 0.9}
[13:03:17] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learner.cc:576: 
Parameters: { "sample_weight", "silent" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


  0%|          | 0/500 [00:00<?, ?trial/s, best loss=?]

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):



[0]	validation_0-merror:0.14314	validation_1-merror:0.18784
[1]	validation_0-merror:0.13201	validation_1-merror:0.17949
[2]	validation_0-merror:0.12588	validation_1-merror:0.17725
[3]	validation_0-merror:0.12148	validation_1-merror:0.17375
[4]	validation_0-merror:0.11942	validation_1-merror:0.17339
[5]	validation_0-merror:0.11542	validation_1-merror:0.17285
[6]	validation_0-merror:0.11212	validation_1-merror:0.17213
[7]	validation_0-merror:0.11082	validation_1-merror:0.17240
[8]	validation_0-merror:0.10786	validation_1-merror:0.17195
[9]	validation_0-merror:0.10617	validation_1-merror:0.17069
[10]	validation_0-merror:0.10476	validation_1-merror:0.17123
[11]	validation_0-merror:0.10377	validation_1-merror:0.17186
[12]	validation_0-merror:0.10218	validation_1-merror:0.17159
[13]	validation_0-merror:0.10049	validation_1-merror:0.17051
[14]	validation_0-merror:0.09596	validation_1-merror:0.17177
[15]	validation_0-merror:0.09349	validation_1-merror:0.17276
[16]	validation_0-merror:0.09172	v

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):



[3]	validation_0-merror:0.17183	validation_1-merror:0.18192                         
[4]	validation_0-merror:0.17172	validation_1-merror:0.17976                         
[5]	validation_0-merror:0.16943	validation_1-merror:0.18093                         
[6]	validation_0-merror:0.16703	validation_1-merror:0.17752                         
[7]	validation_0-merror:0.16595	validation_1-merror:0.17617                         
[8]	validation_0-merror:0.16514	validation_1-merror:0.17527                         
[9]	validation_0-merror:0.16424	validation_1-merror:0.17473                         
[10]	validation_0-merror:0.16247	validation_1-merror:0.17375                        
[11]	validation_0-merror:0.16173	validation_1-merror:0.17330                        
[12]	validation_0-merror:0.16099	validation_1-merror:0.17096                        
[13]	validation_0-merror:0.15962	validation_1-merror:0.17177                        
[14]	validation_0-merror:0.15845	validation_1-merror:0.17141     

...

[0]	validation_0-merror:0.13928	validation_1-merror:0.19610                             
[1]	validation_0-merror:0.12835	validation_1-merror:0.18210                             
[2]	validation_0-merror:0.12326	validation_1-merror:0.17904                             
[3]	validation_0-merror:0.12135	validation_1-merror:0.17635                             
[4]	validation_0-merror:0.12040	validation_1-merror:0.17437                             
[5]	validation_0-merror:0.11643	validation_1-merror:0.17402                             
[6]	validation_0-merror:0.11524	validation_1-merror:0.17285                             
[7]	validation_0-merror:0.11437	validation_1-merror:0.17267                             
[8]	validation_0-merror:0.11293	validation_1-merror:0.16988                             
[9]	validation_0-merror:0.11243	validation_1-merror:0.17042                             
[10]	validation_0-merror:0.11167	validation_1-merror:0.16881                            
[11]	validation_0-mer

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index i

[14:19:48] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learner.cc:576: 
Parameters: { "sample_weight", "silent" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[14:23:29] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learner.cc:576: 
Parameters: { "sample_weight", "silent" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[14:25:32] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learne

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):
/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index i

[42]	validation_0-merror:0.09450	validation_1-merror:0.16647                            
[43]	validation_0-merror:0.09446	validation_1-merror:0.16611                            
[44]	validation_0-merror:0.09419	validation_1-merror:0.16647                            
[45]	validation_0-merror:0.09342	validation_1-merror:0.16638                            
[46]	validation_0-merror:0.09309	validation_1-merror:0.16665                            
[47]	validation_0-merror:0.09293	validation_1-merror:0.16629                            
[48]	validation_0-merror:0.09223	validation_1-merror:0.16620                            
[49]	validation_0-merror:0.09185	validation_1-merror:0.16593                            
[50]	validation_0-merror:0.09163	validation_1-merror:0.16656                            
[51]	validation_0-merror:0.09093	validation_1-merror:0.16665                            
[52]	validation_0-merror:0.09089	validation_1-merror:0.16656                            
[53]	validation_0-mer

In [ ]:
print("The best hyperparameters are: ", "\n")
print(best_hyperparams)

In [29]:
xgb = XGBClassifier(use_label_encoder=False,
                    eval_metric= 'merror',
                    objective= 'multi:softprob',
                    tree_method='gpu_hist',
                    booster= 'gbtree',
                    silent= 1,
                    seed= 42,
                    num_class= 3,
                    sample_weight=sample_weights,
                    colsample_bytree=0.65,
                    eta=0.05,
                    gamma=0.6,
                    max_depth=4,
                    mind_child_weight=4,
                    n_estimators=781,
                    subsample=0.9
                    )

watchlist = [(X_train_, y_train_), (X_val, y_val)]

xgb.fit(X_train_, y_train_, eval_set=watchlist)
y_hat_train = xgb.predict(X_train_)
y_hat = xgb.predict(X_test_)
#
# y_hat = clf.predict(X_test)
print('Train Accuracy score:', accuracy_score(y_hat_train, y_train_))
# # print('Accuracy score:', accuracy_score(y_test, y_hat))
print('Test Accuracy Score:', accuracy_score(y_test_, y_hat))

[12:58:14] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1645117836726/work/src/learner.cc:576: 
Parameters: { "mind_child_weight", "sample_weight", "silent" } might not be used.

  This could be a false alarm, with some parameters getting used by language bindings but
  then being mistakenly passed down to XGBoost core, or some parameter actually being used
  but getting flagged wrongly here. Please open an issue if you find any such cases.


[0]	validation_0-merror:0.23026	validation_1-merror:0.22843
[1]	validation_0-merror:0.22851	validation_1-merror:0.22591
[2]	validation_0-merror:0.23037	validation_1-merror:0.22807
[3]	validation_0-merror:0.22822	validation_1-merror:0.22511
[4]	validation_0-merror:0.21863	validation_1-merror:0.21774
[5]	validation_0-merror:0.21883	validation_1-merror:0.21702
[6]	validation_0-merror:0.21131	validation_1-merror:0.20652
[7]	validation_0-merror:0.21024	validation_1-merror:0.20652
[8]	validation_0-merror:0.21086	validation_1-merror:

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):


[20]	validation_0-merror:0.20054	validation_1-merror:0.19763
[21]	validation_0-merror:0.19845	validation_1-merror:0.19718
[22]	validation_0-merror:0.19843	validation_1-merror:0.19655
[23]	validation_0-merror:0.19814	validation_1-merror:0.19691
[24]	validation_0-merror:0.19697	validation_1-merror:0.19673
[25]	validation_0-merror:0.19690	validation_1-merror:0.19610
[26]	validation_0-merror:0.19618	validation_1-merror:0.19565
[27]	validation_0-merror:0.19551	validation_1-merror:0.19574
[28]	validation_0-merror:0.19522	validation_1-merror:0.19539
[29]	validation_0-merror:0.19446	validation_1-merror:0.19548
[30]	validation_0-merror:0.19419	validation_1-merror:0.19440
[31]	validation_0-merror:0.19360	validation_1-merror:0.19431
[32]	validation_0-merror:0.19295	validation_1-merror:0.19377
[33]	validation_0-merror:0.19246	validation_1-merror:0.19332
[34]	validation_0-merror:0.19239	validation_1-merror:0.19305
[35]	validation_0-merror:0.19259	validation_1-merror:0.19341
[36]	validation_0-merror

In [31]:
test_url = 'https://raw.githubusercontent.com/kyledufrane/Tanzanian_Water_Wells/main/data/Test_set.csv'

In [32]:
test_df_ = test_df[[col for col in X.columns]]
pred = pd.DataFrame(le.inverse_transform(xgb.predict(test_df_)), columns=['status_group'])
sub_idx = pd.DataFrame(pd.read_csv(test_url)['id'])
sub_idx.reset_index(drop=True, inplace=True)
final_sub = pd.concat([sub_idx, pred], axis=1)
final_sub.reset_index(drop=True, inplace=True)
final_sub.set_index('id').to_csv('data/final_sub.csv')

/home/kyle/anaconda3/envs/xgboost/lib/python3.8/site-packages/xgboost/data.py:262: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  elif isinstance(data.columns, (pd.Int64Index, pd.RangeIndex)):
